Task 8.1 Create a bubble map for property crimes in Boston, 2019. Each bubble represents one property crime incident. Your map should look something like this example (Links to an external site.) online. 

First part is just copying what we did earlier to get property crime

In [1]:
import pandas
crime2019 = pandas.read_csv("2019_boston_crime.csv", low_memory=False)
crime2019.dtypes #incident number is mostly int64, but had a few bad pieces of data that ruined it
crime2020 = pandas.read_csv("2020_boston_crime.csv", low_memory=False)
#print(crime2020.dtypes)
combinedCrime = pandas.concat([crime2019, crime2020])
#combinedCrime.describe()
noMissingColumn = ["INCIDENT_NUMBER", "OFFENSE_CODE", "DISTRICT", "Long", "Lat", "SHOOTING", "OCCURRED_ON_DATE"]
for column in noMissingColumn:
    combinedCrime = combinedCrime.query(column + ".notna()")

In [2]:
combinedCrime.describe()

OFFENSE_CODE  OFFENSE_CODE_GROUP       SHOOTING           YEAR  \
count  156759.000000                 0.0  156759.000000  156759.000000   
mean     2321.610479                 NaN       0.012242    2019.450475   
std      1225.696992                 NaN       0.109963       0.497543   
min       100.000000                 NaN       0.000000    2019.000000   
25%       802.000000                 NaN       0.000000    2019.000000   
50%      3005.000000                 NaN       0.000000    2019.000000   
75%      3201.000000                 NaN       0.000000    2020.000000   
max     99999.000000                 NaN       1.000000    2020.000000   

               MONTH           HOUR  UCR_PART            Lat          Long  
count  156759.000000  156759.000000       0.0  156759.000000  1.567590e+05  
mean        6.535076      12.929395       NaN      41.008598 -6.887769e+01  
std         3.377254       6.415094       NaN       7.339247  1.232686e+01  
min         1.000000       0.000000       NaN       0.000000 -7.117867e+01  
25%         4.000000       9.000000       NaN      42.293979 -7.109747e+01  
50%         7.000000      14.000000       NaN      42.324702 -7.107638e+01  
75%         9.000000      18.000000       NaN      42.348010 -7.106045e+01  
max        12.000000      23.000000       NaN      42.395042  5.249691e-08

In [3]:
import numpy as np
#remove dups when those 3 columns are the same, except t0 of each year since that likely means they just didnt have time info
combinedCrime = combinedCrime[np.invert(combinedCrime.duplicated(["OFFENSE_CODE", "OCCURRED_ON_DATE", "STREET"])
                              & [x[5:20] != "01-01 00:00:00" for x in combinedCrime['OCCURRED_ON_DATE']])
                             ].sort_values("OCCURRED_ON_DATE") #DeMorgan's law, !a|b==!(a&!b)
combinedCrime.describe()

OFFENSE_CODE  OFFENSE_CODE_GROUP       SHOOTING           YEAR  \
count  156253.000000                 0.0  156253.000000  156253.000000   
mean     2321.370239                 NaN       0.012256    2019.450046   
std      1226.162631                 NaN       0.110026       0.497500   
min       100.000000                 NaN       0.000000    2019.000000   
25%       802.000000                 NaN       0.000000    2019.000000   
50%      3005.000000                 NaN       0.000000    2019.000000   
75%      3201.000000                 NaN       0.000000    2020.000000   
max     99999.000000                 NaN       1.000000    2020.000000   

               MONTH           HOUR  UCR_PART            Lat          Long  
count  156253.000000  156253.000000       0.0  156253.000000  1.562530e+05  
mean        6.537986      12.933275       NaN      41.006764 -6.887466e+01  
std         3.377193       6.413316       NaN       7.344152  1.233511e+01  
min         1.000000       0.000000       NaN       0.000000 -7.117867e+01  
25%         4.000000       9.000000       NaN      42.293959 -7.109747e+01  
50%         7.000000      14.000000       NaN      42.324702 -7.107638e+01  
75%         9.000000      18.000000       NaN      42.347991 -7.106047e+01  
max        12.000000      23.000000       NaN      42.395042  5.249691e-08

In [4]:
combinedCrime.to_csv("combinedCrime.csv", index=False)

In [5]:
data = pandas.read_csv("combinedCrime.csv", low_memory=False)

In [6]:
codes = pandas.read_excel("rmsoffensecodes.xlsx")

In [7]:
codes.columns

Index(['CODE', 'NAME'], dtype='object')

In [8]:
codes = codes.drop_duplicates()
violentColumns = ["robbery", "assault", "rape"]
violentCodes = []
propertyColumns = ["burglary", "larceny", "theft", "auto theft", "arson"]
propertyCodes = []
violentSum = 0
propertySum = 0
for row in codes.iloc:
    for column in violentColumns:
        if column in row.NAME.lower():
            #violentSum += len(data.query("OFFENSE_CODE == " +  str(row.CODE)))
            #print(row.NAME) #they all looked good
            violentCodes.append(row.CODE)
    for column in propertyColumns:
        if column in row.NAME.lower() and ("force" not in row.NAME.lower() or "no force" in row.NAME.lower()):
            #propertySum += len(data.query("OFFENSE_CODE == " +  str(row.CODE)))
            #print(row.NAME) #some of them used force
            propertyCodes.append(row.CODE)
violenceOrPropValues = ["none", "violence", "property", "both"]
violenceOrProp = []
for x in data["OFFENSE_CODE"]:
    violenceOrProp.append(violenceOrPropValues[int(x in violentCodes) + 2*int(x in propertyCodes)])
data['violenceOrProp'] = violenceOrProp #technically dont have to do this for crosstab

Start of actual new stuff

In [9]:
import pandas as pd
import geopandas as gpd
myGeopandas = gpd.GeoDataFrame(data, geometry=gpd.points_from_xy(data['Long'], data['Lat']))

In [10]:
myGeopandas.head()
#should use folim for mapping apparently

INCIDENT_NUMBER  OFFENSE_CODE  OFFENSE_CODE_GROUP  \
0       192033744          2629                 NaN   
1       192000329           614                 NaN   
2       212013255          1102                 NaN   
3       212012356          2914                 NaN   
4       202011340          2670                 NaN   

                        OFFENSE_DESCRIPTION DISTRICT REPORTING_AREA  SHOOTING  \
0                                HARASSMENT       A1             77         0   
1     LARCENY THEFT FROM MV - NON-ACCESSORY      C11            345         0   
2           FRAUD - FALSE PRETENSE / SCHEME      E18                        0   
3  VAL - OPERATING W/O AUTHORIZATION LAWFUL      C11                        0   
4           HARASSMENT/ CRIMINAL HARASSMENT      C11                        0   

      OCCURRED_ON_DATE  YEAR  MONTH DAY_OF_WEEK  HOUR  UCR_PART  \
0  2019-01-01 00:00:00  2019      1     Tuesday     0       NaN   
1  2019-01-01 00:00:00  2019      1     Tuesday     0       NaN   
2  2019-01-01 00:00:00  2019      1     Tuesday     0       NaN   
3  2019-01-01 00:00:00  2019      1     Tuesday     0       NaN   
4  2019-01-01 00:00:00  2019      1     Tuesday     0       NaN   

           STREET        Lat       Long  \
0  NEW SUDBURY ST  42.361838 -71.059765   
1       HOMES AVE  42.303441 -71.066746   
2  HUNTINGTON AVE  42.256216 -71.124019   
3   CLAYBOURNE ST  42.297555 -71.059709   
4        MORSE ST  42.297555 -71.059709   

                                   Location violenceOrProp  \
0                                    (0, 0)           none   
1                                    (0, 0)       property   
2  (42.256215920402155, -71.12401947329023)           none   
3   (42.29755532959655, -71.05970910242573)           none   
4   (42.29755532959655, -71.05970910242573)           none   

                     geometry  
0  POINT (-71.05976 42.36184)  
1  POINT (-71.06675 42.30344)  
2  POINT (-71.12402 42.25622)  
3  POINT (-71.05971 42.29756)  
4  POINT (-71.05971 42.29756)

In [12]:
print(myGeopandas['Long'].value_counts()) #noticed that some of them have a lat of 0
myGeopandas = myGeopandas.query('Lat != 0')

 0.000000     4855
-71.059709    2539
-71.069409    2258
-71.085634    1778
-71.059765    1648
              ... 
-71.138418       1
-71.054953       1
-71.085447       1
-71.035983       1
-71.054091       1
Name: Long, Length: 27897, dtype: int64


In [13]:
myGeopandas = myGeopandas.query('violenceOrProp == "property" | violenceOrProp == "both"')
startLon, startLat = myGeopandas['Long'].mean(), myGeopandas['Lat'].mean()

In [14]:
pointList = list(zip(myGeopandas.Lat, myGeopandas.Long))
print(len(pointList))

24099


In [15]:
import random
m = folium.Map(location=(startLat, startLon), zoom_start=12, width=800, height=400, tiles="openstreetmap")
#for i in range(len(myGeopandas)):
    #folium.CircleMarker((myGeopandas.loc[i, 'Long'], myGeopandas.loc[i, 'Lat']), opacity=0.7, fill_color='green', weight=2, radius=2).add_to(m)
for point in random.sample(pointList, 6000): #decided to plot 6k/24k of them, to better show density
    folium.Circle(point, opacity=0.7, color='green', weight=2, radius=20).add_to(m)
display(m) #note that the lack of data in brookline and cambridge may have to do with police jurisdiction

Task 8.2: Create another bubble map for violent crimes in Boston, 2019. Use a different map design (marker color, tile style, etc). 

In [16]:
#setup geopandas again, since we filtered it out to just prop rows
myGeopandas = gpd.GeoDataFrame(data, geometry=gpd.points_from_xy(data['Long'], data['Lat']))
myGeopandas = myGeopandas.query('Lat != 0')

In [17]:
myGeopandas = myGeopandas.query('violenceOrProp == "violence" | violenceOrProp == "both"')
startLon, startLat = myGeopandas['Long'].mean(), myGeopandas['Lat'].mean()

In [18]:
pointList = list(zip(myGeopandas.Lat, myGeopandas.Long))
print(len(pointList))

12930


In [19]:
m = folium.Map(location=(startLat, startLon), zoom_start=12, width=800, height=400, tiles="openstreetmap")
for point in random.sample(pointList, 500): #decided to plot 500/24k of them, to better show density
    folium.CircleMarker(point, opacity=0.7, color='red', fill=True, weight=2, radius=6).add_to(m)
display(m) #note that the lack of data in brookline and cambridge may have to do with police jurisdiction

Task 8.3 Calculate zoning district-level violent vs. property crime counts. Use boston's zoning map from here (Links to an external site.) to map individual crime incidents to zoning district. Create a bubble map for these two sets of counts. There should be two sets of bubbles in your map. One set represents district-level violent crime counts, and the other set district-level property crime counts. These two bubble sets should be colored differently, but the size of the bubble for both sets should indicate the relative size of the crime count. Use each district’s centroid location to place their bubbles on the map.

In [20]:
import os
os.chdir(r'C:/Users/SLdra/Documents/Me/BC/Advance/Data/jupyter/exercise8')
zoneData = gpd.read_file('Boston_Zoning_Subdistricts.geojson')

In [21]:
print(zoneData.columns)
zoneData.describe()

Index(['OBJECTID', 'ZONE_', 'DISTRICT', 'MAPNO', 'ARTICLE', 'SUBDISTRIC',
       'Unique_Code', 'FAR', 'Zone_Desc', 'Shape_STArea_1', 'Shape_STLength_1',
       'Urban_Label', 'Shape__Area', 'Shape__Length', 'geometry'],
      dtype='object')


OBJECTID          FAR  Shape_STArea_1  Shape_STLength_1  \
count  1649.000000  1197.000000    1.649000e+03       1649.000000   
mean   4127.916313     1.931821    1.303022e+06       4262.505331   
std     476.302535     2.258602    1.377641e+07       6282.851042   
min    3303.000000     0.300000    9.808350e+02        146.013511   
25%    3716.000000     0.600000    5.065362e+04       1065.419611   
50%    4128.000000     1.000000    1.882932e+05       2332.435604   
75%    4540.000000     2.000000    6.735309e+05       4928.268806   
max    4952.000000    17.500000    5.391227e+08      95668.484944   

        Shape__Area  Shape__Length  
count  1.649000e+03    1649.000000  
mean   1.303004e+06    4264.261719  
std    1.377639e+07    6281.770606  
min    9.808350e+02     146.013511  
25%    5.074789e+04    1066.127092  
50%    1.883610e+05    2335.055917  
75%    6.735309e+05    4928.268806  
max    5.391227e+08   95668.484944

In [22]:
#setup geopandas again, since we filtered it out to just prop rows
myGeopandas = gpd.GeoDataFrame(data, geometry=gpd.points_from_xy(data['Long'], data['Lat']))
myGeopandas = myGeopandas.query('Lat != 0')
myGeopandas.head()
myGeopandas.set_crs(epsg=4326, inplace=True)

INCIDENT_NUMBER  OFFENSE_CODE  OFFENSE_CODE_GROUP  \
0            192033744          2629                 NaN   
1            192000329           614                 NaN   
2            212013255          1102                 NaN   
3            212012356          2914                 NaN   
4            202011340          2670                 NaN   
...                ...           ...                 ...   
156247       212000542           619                 NaN   
156248       202095668          3802                 NaN   
156249       202095647          1402                 NaN   
156251       212000339           801                 NaN   
156252       212000003          3114                 NaN   

                             OFFENSE_DESCRIPTION DISTRICT REPORTING_AREA  \
0                                     HARASSMENT       A1             77   
1          LARCENY THEFT FROM MV - NON-ACCESSORY      C11            345   
2                FRAUD - FALSE PRETENSE / SCHEME      E18                  
3       VAL - OPERATING W/O AUTHORIZATION LAWFUL      C11                  
4                HARASSMENT/ CRIMINAL HARASSMENT      C11                  
...                                          ...      ...            ...   
156247                        LARCENY ALL OTHERS      A15             41   
156248            M/V ACCIDENT - PROPERTY DAMAGE       B2            257   
156249                                 VANDALISM       B3            454   
156251                          ASSAULT - SIMPLE       A1             77   
156252                      INVESTIGATE PROPERTY      C11            436   

        SHOOTING     OCCURRED_ON_DATE  YEAR  MONTH DAY_OF_WEEK  HOUR  \
0              0  2019-01-01 00:00:00  2019      1     Tuesday     0   
1              0  2019-01-01 00:00:00  2019      1     Tuesday     0   
2              0  2019-01-01 00:00:00  2019      1     Tuesday     0   
3              0  2019-01-01 00:00:00  2019      1     Tuesday     0   
4              0  2019-01-01 00:00:00  2019      1     Tuesday     0   
...          ...                  ...   ...    ...         ...   ...   
156247         0  2020-12-31 22:50:00  2020     12    Thursday    22   
156248         0  2020-12-31 22:59:00  2020     12    Thursday    22   
156249         0  2020-12-31 23:04:00  2020     12    Thursday    23   
156251         0  2020-12-31 23:40:00  2020     12    Thursday    23   
156252         1  2020-12-31 23:55:00  2020     12    Thursday    23   

        UCR_PART          STREET        Lat       Long  \
0            NaN  NEW SUDBURY ST  42.361838 -71.059765   
1            NaN       HOMES AVE  42.303441 -71.066746   
2            NaN  HUNTINGTON AVE  42.256216 -71.124019   
3            NaN   CLAYBOURNE ST  42.297555 -71.059709   
4            NaN        MORSE ST  42.297555 -71.059709   
...          ...             ...        ...        ...   
156247       NaN        SPICE ST  42.376632 -71.055932   
156248       NaN    STOUGHTON ST  42.316617 -71.064078   
156249       NaN       RIPLEY RD  42.299263 -71.076265   
156251       NaN        BROAD ST  42.361839 -71.059765   
156252       NaN   WASHINGTON ST  42.287830 -71.071193   

                                        Location violenceOrProp  \
0                                         (0, 0)           none   
1                                         (0, 0)       property   
2       (42.256215920402155, -71.12401947329023)           none   
3        (42.29755532959655, -71.05970910242573)           none   
4        (42.29755532959655, -71.05970910242573)           none   
...                                          ...            ...   
156247     (42.3766316681323, -71.0559319549787)       property   
156248     (42.3166174973565, -71.0640782725732)           none   
156249     (42.2992630326008, -71.0762651335127)           none   
156251     (42.3618385665647, -71.0597648909416)       violence   
156252     (42.2878296258842, -71.0711928171256)           none   

      

In [23]:
districtCrime = gpd.sjoin(myGeopandas, zoneData, predicate='within', how='left')

In [24]:
propDistrictCount = districtCrime.query('violenceOrProp == "property" | violenceOrProp == "both"').groupby('OBJECTID').agg('INCIDENT_NUMBER').count().reset_index()

In [25]:
propDistrictCount #seems like only 2/3 of the districts had prop crime

OBJECTID  INCIDENT_NUMBER
0      3303.0                3
1      3304.0                3
2      3305.0                8
3      3306.0                6
4      3307.0                5
..        ...              ...
971    4946.0                4
972    4947.0                8
973    4949.0               13
974    4951.0               35
975    4952.0               35

[976 rows x 2 columns]

In [26]:
violentDistrictCount = districtCrime.query('violenceOrProp == "property" | violenceOrProp == "both"').groupby('OBJECTID').agg('INCIDENT_NUMBER').count().reset_index()

In [27]:
violentDistrictCount = zoneData[['OBJECTID', 'geometry']].merge(violentDistrictCount, how='inner', on='OBJECTID')
violentDistrictCount.head()
#districtCrime.to_crs('cea', inplace=True)
#districtCrime.to_crs('+proj=cea')

OBJECTID                                           geometry  \
0      3303  POLYGON ((-71.09452 42.33244, -71.09465 42.332...   
1      3304  POLYGON ((-71.03554 42.33992, -71.03556 42.340...   
2      3305  POLYGON ((-71.04214 42.34626, -71.04545 42.347...   
3      3306  POLYGON ((-71.04143 42.34455, -71.04060 42.345...   
4      3307  POLYGON ((-71.03770 42.33812, -71.03725 42.338...   

   INCIDENT_NUMBER  
0                3  
1                3  
2                8  
3                6  
4                5

In [29]:
violentDistrictCount

OBJECTID                                           geometry  \
0        3303  POLYGON ((-71.09452 42.33244, -71.09465 42.332...   
1        3304  POLYGON ((-71.03554 42.33992, -71.03556 42.340...   
2        3305  POLYGON ((-71.04214 42.34626, -71.04545 42.347...   
3        3306  POLYGON ((-71.04143 42.34455, -71.04060 42.345...   
4        3307  POLYGON ((-71.03770 42.33812, -71.03725 42.338...   
..        ...                                                ...   
971      4946  POLYGON ((-71.09855 42.32421, -71.09862 42.324...   
972      4947  POLYGON ((-71.11237 42.30152, -71.11219 42.301...   
973      4949  POLYGON ((-71.11419 42.30153, -71.11418 42.301...   
974      4951  POLYGON ((-71.04241 42.31790, -71.04319 42.318...   
975      4952  POLYGON ((-71.04241 42.31790, -71.04319 42.318...   

     INCIDENT_NUMBER  
0                  3  
1                  3  
2                  8  
3                  6  
4                  5  
..               ...  
971                4  
972                8  
973               13  
974               35  
975               35  

[976 rows x 3 columns]

In [35]:
m = folium.Map(location=(startLat, startLon), zoom_start=12, width=800, height=400, tiles="openstreetmap")
for row in violentDistrictCount.iloc:
    coords = list(row['geometry'].centroid.coords)
    coords = coords[0] #gives long, lat
    #radius of 0 still gives a circle
    #bc radius is in proportion to sqrt of area, made it sqrt here to be accurate
    folium.CircleMarker((coords[1], coords[0]), opacity=0.7, color='red', fill=True, weight=1, radius=row['INCIDENT_NUMBER']**0.5).add_to(m)
display(m) #note that the lack of data in brookline and cambridge may have to do with police jurisdiction